<h2>An introduction to using python to access Madrigal data (madrigalWeb)</h2>

This notebook available at http://www.haystack.mit.edu/~brideout/Madrigal_python_demo.ipynb

To download the latest Python Madrigal API, go to http://cedar.openmadrigal.org/madrigalDownload/, or use pip:

<pre>pip install madrigalWeb</pre>

This module should work with either python 2 or python 3.

Then feel free to follow along with this talk!

Url of present Madrigal CEDAR database: http://cedar.openmadrigal.org
Url of Madrigal 3 CEDAR database beta site: http://madrigal3.haystack.mit.edu

When Madrigal 3 is released, http://cedar.openmadrigal.org will be Madrigal 3.

Online resources: <a href="http://madrigal3.haystack.mit.edu/rt_python.html">Tutorial</a> and <a href="http://madrigal3.haystack.mit.edu/rr_python.html">Reference</a>

Any questions: Email me (Bill Rideout) at <a href="mailto:brideout@haystack.mit.edu">brideout@haystack.mit.edu</a>

In [1]:
import madrigalWeb.madrigalWeb

The next command connects to one particular Madrigal site, and creates an object we will use for the rest of the session.

In [2]:
madDB = madrigalWeb.madrigalWeb.MadrigalData('http://madrigal.haystack.mit.edu/madrigal')

The top level of metadata at any site is the instruments it has available. This next method lists the available instruments.

In [3]:
instList = madDB.getAllInstruments()

In [4]:
print(instList[7])

name: Millstone Hill IS Radar
code: 30
mnemonic: mlh
latitude: 42.619
longitude: 288.51
altitude: 0.146
category: Incoherent Scatter Radars



Note that the code associated with the Millstone Hill IS Radar is 30 (not related to its position in the list, which may change).  Also refered to as the kinst.  This will be used throughout the rest of the calls to refer to this instrument.

The next call gets all the experiments with that instrument over the date range of January 2016:

In [5]:
exps = madDB.getExperiments(30, 2016,1,1,0,0,0,2016,2,1,0,0,0)

In [6]:
print(exps[0])

id: 10003086
realUrl: http://madrigal.haystack.mit.edu/cgi-bin/madrigal/madExperiment.cgi?exp=experiments/2016/mlh/25jan16&displayLevel=0&expTitle=SWARM
url: http://madrigal.haystack.mit.edu/cgi-bin/madrigal/madtoc/experiments/2016/mlh/25jan16
name: SWARM
siteid: 1
sitename: Millstone
instcode: 30
instname: Millstone Hill IS Radar
startyear: 2016
startmonth: 1
startday: 25
starthour: 17
startmin: 15
startsec: 59
endyear: 2016
endmonth: 1
endday: 26
endhour: 2
endmin: 28
endsec: 34
isLocal: True
madrigalUrl: http://madrigal.haystack.mit.edu/madrigal
PI: Phil Erickson
PIEmail: perickson@haystack.mit.edu
uttimestamp: 1470879969
access: 0
Madrigal version: 2.6.4



In [7]:
len(exps)

6

The next call gets all the files in that experiment.  An experiment may contain different types of data, as will be described in the kind of data description (kindatdesc):

In [8]:
files = madDB.getExperimentFiles(exps[0].id)

In [9]:
print(files[0])

name: /opt/madrigal/experiments/2016/mlh/25jan16/mlh160125g.005
kindat: 3410
kindatdesc: Combined basic parameters file - all antennas and modes
category: 1
status: Final
permission: 0
expId: 10003086
doi: None



As a simple example, let's just download this data as is.  You could also filter the data, add derived parameters, and select the parameters you want using other calls.  

Because Madrigal is not login controlled, logging is done by you passing in unverified identification information - your name, email, and affiliation.  Below I set up my personal info - <b>please change this to yours when you use this API!</b>

In [10]:
user_fullname = 'Bill Rideout' 
user_email = 'brideout@haystack.mit.edu' 
user_affiliation= 'MIT'

In [11]:
madDB.downloadFile(files[0].name, '/tmp/test.hdf5', user_fullname, user_email, user_affiliation, format='hdf5')

Now let's say I wanted to know what parameters were in this file.  You can get that from the API also:

In [12]:
parms = madDB.getExperimentFileParameters(files[0].name)

In [13]:
print(parms[25])

mnemonic: WCHSQI
description: Additional increment to wide chi sq
isError: 0
units: N/A
isMeasured: 1
category: Data Quality Parameter
isSure: 1
isAddIncrement: 1



In the next command we are going to download data from that file with the parameters we select, and the filters we want to remove unwanted data.  A list of all valid CEDAR Madrigal parameters can be found at http://madrigal3.haystack.mit.edu/parameterMetadata/.  A description of how to write filter strings are at http://madrigal3.haystack.mit.edu/filterMetadata/ .

In this example, we will choose the parameters YEAR,MONTH,DAY,HOUR,MIN,SEC,AZM,ELM,RANGE,GDALT,GLON,GDALT,TI,DTI. The filters will limit gdalt to between 200 and 300, and we will only look at data where DTI < 10 degrees. Our filter string is then "filter=gdalt,200,300 filter=dti,,10" The blank in dti means no lower limit.

In [14]:
filterStr="filter=gdalt,200,300 filter=dti,,10"
parms = "YEAR,MONTH,DAY,HOUR,MIN,SEC,AZM,ELM,RANGE,GDALT,GLON,GDALT,TI,DTI"
result = madDB.isprint(files[0].name, parms, filterStr, user_fullname, user_email, user_affiliation)

In [15]:
lines = result.split('\n')
for line in lines[:5]:
    print(line)


  2016         1        25        17        17        29       178.00      88.00     213.57     213.57     -71.49     213.57      919.0        1.0  
  2016         1        25        17        17        29       178.00      88.00     231.56     231.54     -71.49     231.54      891.0        6.0  
  2016         1        25        17        17        29       178.00      88.00     249.55     249.52     -71.49     249.52      871.0        5.0  
  2016         1        25        17        17        29       178.00      88.00     267.53     267.49     -71.49     267.49      876.0        2.0  
